<img src="../input/head.png" alt="header">

# Part II: Model Building and Validation

In [1]:
import numpy as np
import pandas as pd
pd.set_option("display.max_columns", None)

import plotly.express as px

import optuna
# import optuna.logging as optuna_logging
# optuna_logging.set_verbosity(optuna.logging.WARNING)

rs=17

### Getting Data

#### Data import

In [2]:
X = pd.read_csv("../output/X.csv")
y = np.ravel(pd.read_csv("../output/y.csv"))
X_t = pd.read_csv("../output/X_test.csv")
sample_submission = pd.read_csv("../input/playground-series-s3e14/sample_submission.csv")

In [3]:
# Help from this discussion: https://www.kaggle.com/competitions/playground-series-s3e14/discussion/407327
unique_targets = np.unique(y)
unique_targets.shape

(776,)

In [ ]:
# import lightgbm as lgb
# from sklearn.metrics import mean_absolute_error
# from sklearn.model_selection import KFold
# import optuna
# import numpy as np

# study_name = "LGBR-1/KF8"
# n_trials = 40
# n_splits = 7
# early_stopping_rounds = 450

# # Define the objective function
# def objective(trial):
#     params = {
#         'objective': 'regression_l1',
#         'metric': 'mean_absolute_error',
#         'max_depth': trial.suggest_int('max_depth', 3, 12),
#         'num_leaves': trial.suggest_int('num_leaves', 40, 60),
#         'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
#         'subsample': trial.suggest_float('subsample', 0.5, 1.0),
#         'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
#         'min_child_weight': trial.suggest_int('min_child_weight', 1, 5),
#         'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
#         'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
#         'verbosity': -1,
#     }
    
#     model = lgb.LGBMRegressor(**params, n_estimators=10000, random_state=rs)
#     mae_scores = []
#     kf = KFold(n_splits=n_splits, shuffle=True, random_state=rs)

#     for train_index, test_index in kf.split(X):
#         X_train, X_test = X.iloc[train_index], X.iloc[test_index]
#         y_train, y_test = y[train_index], y[test_index]

#         dtrain = lgb.Dataset(X_train, label=y_train)
#         dtest = lgb.Dataset(X_test, label=y_test)

#         callbacks = [lgb.early_stopping(early_stopping_rounds, verbose=True)]

#         model = lgb.train(
#             params,
#             dtrain,
#             num_boost_round=10000,
#             valid_sets=[dtrain, dtest],
#             callbacks=callbacks,
#         )

#         y_pred = model.predict(X_test)
#         mae_scores.append(mean_absolute_error(y_test, y_pred))

#     mean_mae = np.mean(mae_scores)
#     return mean_mae

# # Create the study and optimize
# study = optuna.create_study(study_name=study_name, direction='minimize')
# study.optimize(objective, n_trials=n_trials)

# # Print the best trial and its score
# print(f"Best trial for LGBR1: {study.best_trial.params}")
# print(f"Best MAE score for LGBR1: {study.best_value}")

# # Get the best parameters
# best_params_lgbr1 = study.best_trial.params

# # Plot the study
# optuna.visualization.plot_optimization_history(study)

In [ ]:
# preds = lgb.LGBMRegressor(**best_params_lgbr1, n_estimators=10000, random_state=rs).fit(X, y).predict(X_t)

In [ ]:
# # create copies of the arrays
# unique_targets_c = np.copy(unique_targets)
# preds_c = np.copy(preds)

# # find the nearest value from the first array for each element in the second array
# nearest_values = unique_targets_c[np.abs(unique_targets_c - preds_c[:, np.newaxis]).argmin(axis=1)]

# # calculate the deviation of each element in the second array from its nearest value
# deviations = np.sign(preds_c - nearest_values) * np.abs(preds_c - nearest_values)

# # create the new array with replaced values
# preds_replaced = nearest_values

# # plot the deviations
# px.line(deviations)

In [ ]:
# px.histogram(preds)

In [ ]:
# px.histogram(preds_replaced)

In [ ]:
# px.histogram(deviations)

In [ ]:
# deviations.std()

In [ ]:
# px.scatter(x=preds, y=deviations)

In [ ]:
# px.scatter(x=preds, y=preds_replaced, color=deviations)

In [ ]:
# submission = pd.DataFrame({'id': sample_submission.id, 'yield': preds})
# submission.to_csv('../submissions/submission_6_O.csv', index=False)

LB: 420.55434 (Worse)

In [ ]:
# # kaggle submission file
# submission = pd.DataFrame({'id': sample_submission.id, 'yield': preds_replaced})
# submission.to_csv('../submissions/submission_6_R.csv', index=False)

LB: 420.37965

In [5]:
from xgboost import XGBRegressor
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import KFold

study_name = "XGBR-1/KF7"
n_trials = 40
n_splits = 7

# Define the objective function
def objective(trial):
    params = {
        'max_depth': trial.suggest_int('max_depth', 3, 9),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'min_child_weight': trial.suggest_int('min_child_weight', 1, 5),
        'gamma': trial.suggest_float('gamma', 0.0, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
        'verbosity': 0,
        'objective': 'reg:squarederror'
    }
    
    model = XGBRegressor(**params, random_state=rs)
    mae_scores = []
    kf = KFold(n_splits=n_splits, shuffle=True, random_state=rs)
    
    for train_index, test_index in kf.split(X):
        X_train, X_test = X.iloc[train_index], X.iloc[test_index]
        y_train, y_test = y[train_index], y[test_index]
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        mae_scores.append(mean_absolute_error(y_test, y_pred))

    mean_mae = np.mean(mae_scores)
    return mean_mae

# Create the study and optimize
study = optuna.create_study(study_name=study_name, direction='minimize')
study.optimize(objective, n_trials=n_trials)

# Print the best trial and its score
print(f"Best trial for XGBR1: {study.best_trial.params}")
print(f"Best MAE score for XGBR1: {study.best_value}")

# Get the best parameters
best_params_xgbr1 = study.best_trial.params

# Plot the study
optuna.visualization.plot_optimization_history(study)

[I 2023-05-11 07:43:56,237] A new study created in memory with name: XGBR-1/KF7
[I 2023-05-11 07:44:01,192] Trial 0 finished with value: 355.67460734480335 and parameters: {'max_depth': 4, 'learning_rate': 0.08254119568913566, 'subsample': 0.5356623397802205, 'colsample_bytree': 0.5243246727707542, 'min_child_weight': 4, 'gamma': 0.8282356128364162, 'reg_alpha': 0.6046319126688807, 'reg_lambda': 0.33772022511661937}. Best is trial 0 with value: 355.67460734480335.
[I 2023-05-11 07:44:11,097] Trial 1 finished with value: 1642.2779760312085 and parameters: {'max_depth': 6, 'learning_rate': 0.013002167021808937, 'subsample': 0.9484901781328108, 'colsample_bytree': 0.842713738410821, 'min_child_weight': 5, 'gamma': 0.5147222652300308, 'reg_alpha': 0.6301372632099694, 'reg_lambda': 0.2234421234098296}. Best is trial 0 with value: 355.67460734480335.
[I 2023-05-11 07:44:23,840] Trial 2 finished with value: 1066.4327136328689 and parameters: {'max_depth': 9, 'learning_rate': 0.017518669522056

[I 2023-05-11 07:47:35,361] Trial 21 finished with value: 350.9261245201669 and parameters: {'max_depth': 6, 'learning_rate': 0.05332238537573984, 'subsample': 0.8223697566262506, 'colsample_bytree': 0.9302602101771196, 'min_child_weight': 2, 'gamma': 0.12227447438760988, 'reg_alpha': 0.29257243080768364, 'reg_lambda': 0.8049153226271143}. Best is trial 20 with value: 350.8525540312456.
[I 2023-05-11 07:47:45,495] Trial 22 finished with value: 351.2684644563511 and parameters: {'max_depth': 6, 'learning_rate': 0.050961605544598415, 'subsample': 0.8172276023081839, 'colsample_bytree': 0.9436651870490668, 'min_child_weight': 3, 'gamma': 0.1180230254860903, 'reg_alpha': 0.3641859311208863, 'reg_lambda': 0.8336486474600155}. Best is trial 20 with value: 350.8525540312456.
[I 2023-05-11 07:47:55,610] Trial 23 finished with value: 351.02515212771306 and parameters: {'max_depth': 6, 'learning_rate': 0.051447358939351, 'subsample': 0.8162473079278806, 'colsample_bytree': 0.9397790641103476, 'm

Best trial for XGBR1: {'max_depth': 6, 'learning_rate': 0.06347576855559214, 'subsample': 0.7830202184419717, 'colsample_bytree': 0.8389341524955048, 'min_child_weight': 2, 'gamma': 0.18921359915094105, 'reg_alpha': 0.5848209345410538, 'reg_lambda': 0.8303681326724046}
Best MAE score for XGBR1: 350.69440027616463


In [6]:
preds_xgbr = XGBRegressor(**best_params_xgbr1, random_state=rs).fit(X, y).predict(X_t)

In [9]:
from catboost import CatBoostRegressor
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import KFold
import optuna
import numpy as np

study_name = "CatBoostR-1/KF7"
n_trials = 40
n_splits = 7

# Define the objective function
def objective(trial):
    params = {
        'depth': trial.suggest_int('depth', 8, 20),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'grow_policy': 'Lossguide',
        'colsample_bylevel': trial.suggest_float('colsample_bylevel', 0.5, 1.0),
        'min_child_samples': trial.suggest_int('min_child_samples', 1, 5),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 0.0, 1.0),
        'bootstrap_type': 'Bayesian',
        'eval_metric': 'MAE',
        'loss_function': 'MAE',
        'silent': True,
        'random_seed': rs
    }

    model = CatBoostRegressor(**params)
    mae_scores = []
    kf = KFold(n_splits=n_splits, shuffle=True, random_state=rs)
    
    for train_index, test_index in kf.split(X):
        X_train, X_test = X.iloc[train_index], X.iloc[test_index]
        y_train, y_test = y[train_index], y[test_index]
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        mae_scores.append(mean_absolute_error(y_test, y_pred))

    mean_mae = np.mean(mae_scores)
    return mean_mae

# Create the study and optimize
study = optuna.create_study(study_name=study_name, direction='minimize')
study.optimize(objective, n_trials=n_trials)

# Print the best trial and its score
print(f"Best trial for CatBoostR1: {study.best_trial.params}")
print(f"Best MAE score for CatBoostR1: {study.best_value}")

# Get the best parameters
best_params_catboost_r1 = study.best_trial.params

# Plot the study
optuna.visualization.plot_optimization_history(study)

[I 2023-05-11 07:54:14,725] A new study created in memory with name: CatBoostR-1/KF7
[I 2023-05-11 07:55:40,900] Trial 0 finished with value: 344.0807233243772 and parameters: {'depth': 12, 'learning_rate': 0.07968668582949667, 'colsample_bylevel': 0.582935355979748, 'min_child_samples': 3, 'l2_leaf_reg': 0.6672740237743984}. Best is trial 0 with value: 344.0807233243772.
[I 2023-05-11 07:57:17,949] Trial 1 finished with value: 343.36242145921653 and parameters: {'depth': 12, 'learning_rate': 0.07672768135021595, 'colsample_bylevel': 0.8019290304183837, 'min_child_samples': 5, 'l2_leaf_reg': 0.9261828056425179}. Best is trial 1 with value: 343.36242145921653.
[I 2023-05-11 07:59:06,638] Trial 2 finished with value: 342.820236800598 and parameters: {'depth': 18, 'learning_rate': 0.07835034027736358, 'colsample_bylevel': 0.8952721639463161, 'min_child_samples': 5, 'l2_leaf_reg': 0.9170967448205186}. Best is trial 2 with value: 342.820236800598.
[I 2023-05-11 08:00:58,047] Trial 3 finishe

[I 2023-05-11 08:43:09,243] Trial 27 finished with value: 341.29148848628245 and parameters: {'depth': 14, 'learning_rate': 0.033605051585328095, 'colsample_bylevel': 0.8788566852608073, 'min_child_samples': 4, 'l2_leaf_reg': 0.6007441457816919}. Best is trial 20 with value: 341.14551038843035.
[I 2023-05-11 08:44:54,968] Trial 28 finished with value: 342.3028650167799 and parameters: {'depth': 18, 'learning_rate': 0.017214567892189808, 'colsample_bylevel': 0.8309442224378817, 'min_child_samples': 3, 'l2_leaf_reg': 0.47244336040595797}. Best is trial 20 with value: 341.14551038843035.
[I 2023-05-11 08:46:45,569] Trial 29 finished with value: 342.00558410490186 and parameters: {'depth': 16, 'learning_rate': 0.021341017951415176, 'colsample_bylevel': 0.9085056257370483, 'min_child_samples': 3, 'l2_leaf_reg': 0.6455370948334025}. Best is trial 20 with value: 341.14551038843035.
[I 2023-05-11 08:48:35,104] Trial 30 finished with value: 341.94577139957363 and parameters: {'depth': 19, 'lear

Best trial for CatBoostR1: {'depth': 15, 'learning_rate': 0.03765914255287735, 'colsample_bylevel': 0.8864241556650356, 'min_child_samples': 4, 'l2_leaf_reg': 0.7134060056212908}
Best MAE score for CatBoostR1: 341.14180282744024


In [10]:
preds_cbr = CatBoostRegressor(**best_params_catboost_r1, random_state=rs).fit(X, y).predict(X_t)

0:	learn: 1297.5120961	total: 620ms	remaining: 10m 19s
1:	learn: 1259.9154181	total: 644ms	remaining: 5m 21s
2:	learn: 1224.7136352	total: 1.21s	remaining: 6m 40s
3:	learn: 1190.2031656	total: 1.83s	remaining: 7m 34s
4:	learn: 1157.5282229	total: 2.41s	remaining: 7m 59s
5:	learn: 1127.4484291	total: 2.48s	remaining: 6m 51s
6:	learn: 1097.7396698	total: 2.5s	remaining: 5m 54s
7:	learn: 1069.7255414	total: 3.07s	remaining: 6m 20s
8:	learn: 1042.6497602	total: 3.08s	remaining: 5m 39s
9:	learn: 1016.5550213	total: 3.69s	remaining: 6m 5s
10:	learn: 991.6738801	total: 3.73s	remaining: 5m 35s
11:	learn: 967.7197562	total: 4.24s	remaining: 5m 49s
12:	learn: 945.1771802	total: 4.31s	remaining: 5m 27s
13:	learn: 923.2572006	total: 4.89s	remaining: 5m 44s
14:	learn: 902.6077187	total: 5.45s	remaining: 5m 58s
15:	learn: 882.9464013	total: 5.49s	remaining: 5m 37s
16:	learn: 864.5562427	total: 5.53s	remaining: 5m 19s
17:	learn: 846.7209090	total: 6.04s	remaining: 5m 29s
18:	learn: 829.7084868	total:

152:	learn: 444.7330812	total: 1m 23s	remaining: 7m 44s
153:	learn: 444.3141939	total: 1m 24s	remaining: 7m 44s
154:	learn: 443.8965234	total: 1m 25s	remaining: 7m 45s
155:	learn: 443.2074004	total: 1m 26s	remaining: 7m 45s
156:	learn: 442.4674120	total: 1m 26s	remaining: 7m 46s
157:	learn: 441.8572450	total: 1m 27s	remaining: 7m 46s
158:	learn: 441.2582446	total: 1m 28s	remaining: 7m 47s
159:	learn: 440.7863354	total: 1m 28s	remaining: 7m 47s
160:	learn: 439.9677810	total: 1m 29s	remaining: 7m 47s
161:	learn: 439.4371210	total: 1m 30s	remaining: 7m 47s
162:	learn: 438.8855483	total: 1m 30s	remaining: 7m 47s
163:	learn: 438.6275916	total: 1m 31s	remaining: 7m 46s
164:	learn: 438.1042300	total: 1m 32s	remaining: 7m 46s
165:	learn: 436.8109926	total: 1m 32s	remaining: 7m 46s
166:	learn: 436.1215125	total: 1m 33s	remaining: 7m 46s
167:	learn: 435.8183171	total: 1m 33s	remaining: 7m 44s
168:	learn: 435.5893749	total: 1m 34s	remaining: 7m 45s
169:	learn: 435.2545855	total: 1m 35s	remaining:

300:	learn: 364.6893358	total: 2m 56s	remaining: 6m 49s
301:	learn: 364.1362527	total: 2m 56s	remaining: 6m 48s
302:	learn: 363.3788811	total: 2m 57s	remaining: 6m 48s
303:	learn: 363.0619200	total: 2m 58s	remaining: 6m 48s
304:	learn: 362.7795161	total: 2m 58s	remaining: 6m 47s
305:	learn: 361.8283255	total: 2m 59s	remaining: 6m 47s
306:	learn: 361.6435227	total: 3m	remaining: 6m 46s
307:	learn: 361.2622239	total: 3m	remaining: 6m 46s
308:	learn: 360.8117754	total: 3m 1s	remaining: 6m 45s
309:	learn: 360.5394544	total: 3m 2s	remaining: 6m 45s
310:	learn: 359.9300639	total: 3m 2s	remaining: 6m 44s
311:	learn: 359.3667111	total: 3m 3s	remaining: 6m 44s
312:	learn: 358.9291670	total: 3m 4s	remaining: 6m 44s
313:	learn: 358.5201315	total: 3m 4s	remaining: 6m 43s
314:	learn: 358.1724807	total: 3m 5s	remaining: 6m 43s
315:	learn: 357.9305421	total: 3m 6s	remaining: 6m 42s
316:	learn: 357.2898234	total: 3m 6s	remaining: 6m 42s
317:	learn: 356.6345871	total: 3m 7s	remaining: 6m 41s
318:	learn

448:	learn: 301.9227140	total: 4m 34s	remaining: 5m 36s
449:	learn: 301.4018664	total: 4m 35s	remaining: 5m 36s
450:	learn: 301.0666592	total: 4m 35s	remaining: 5m 35s
451:	learn: 300.6100426	total: 4m 36s	remaining: 5m 35s
452:	learn: 299.8295393	total: 4m 37s	remaining: 5m 34s
453:	learn: 299.4424183	total: 4m 37s	remaining: 5m 34s
454:	learn: 299.1473971	total: 4m 38s	remaining: 5m 33s
455:	learn: 298.8078011	total: 4m 39s	remaining: 5m 33s
456:	learn: 298.3804306	total: 4m 39s	remaining: 5m 32s
457:	learn: 298.0001615	total: 4m 40s	remaining: 5m 31s
458:	learn: 297.3042110	total: 4m 41s	remaining: 5m 31s
459:	learn: 297.0239154	total: 4m 41s	remaining: 5m 30s
460:	learn: 296.3282661	total: 4m 42s	remaining: 5m 30s
461:	learn: 295.9444974	total: 4m 43s	remaining: 5m 29s
462:	learn: 295.6206892	total: 4m 44s	remaining: 5m 29s
463:	learn: 294.9648603	total: 4m 44s	remaining: 5m 29s
464:	learn: 294.8345216	total: 4m 45s	remaining: 5m 28s
465:	learn: 294.4680029	total: 4m 46s	remaining:

596:	learn: 255.4519899	total: 6m 14s	remaining: 4m 12s
597:	learn: 255.1722804	total: 6m 15s	remaining: 4m 12s
598:	learn: 254.9530664	total: 6m 15s	remaining: 4m 11s
599:	learn: 254.5440404	total: 6m 16s	remaining: 4m 11s
600:	learn: 254.4378919	total: 6m 17s	remaining: 4m 10s
601:	learn: 253.8209851	total: 6m 17s	remaining: 4m 9s
602:	learn: 253.2207122	total: 6m 18s	remaining: 4m 9s
603:	learn: 252.8625505	total: 6m 19s	remaining: 4m 8s
604:	learn: 252.3242815	total: 6m 19s	remaining: 4m 7s
605:	learn: 251.9931260	total: 6m 20s	remaining: 4m 7s
606:	learn: 251.4843382	total: 6m 21s	remaining: 4m 6s
607:	learn: 251.1839125	total: 6m 21s	remaining: 4m 6s
608:	learn: 250.9016953	total: 6m 22s	remaining: 4m 5s
609:	learn: 250.3534126	total: 6m 22s	remaining: 4m 4s
610:	learn: 250.2726527	total: 6m 23s	remaining: 4m 4s
611:	learn: 249.9968698	total: 6m 24s	remaining: 4m 3s
612:	learn: 249.9026644	total: 6m 24s	remaining: 4m 2s
613:	learn: 249.7100392	total: 6m 25s	remaining: 4m 2s
614:	

744:	learn: 216.6760697	total: 7m 50s	remaining: 2m 41s
745:	learn: 216.4392717	total: 7m 51s	remaining: 2m 40s
746:	learn: 216.2313403	total: 7m 52s	remaining: 2m 39s
747:	learn: 215.8465580	total: 7m 52s	remaining: 2m 39s
748:	learn: 215.7190898	total: 7m 53s	remaining: 2m 38s
749:	learn: 215.4595008	total: 7m 53s	remaining: 2m 37s
750:	learn: 215.4187141	total: 7m 54s	remaining: 2m 37s
751:	learn: 215.1140750	total: 7m 55s	remaining: 2m 36s
752:	learn: 214.7199557	total: 7m 55s	remaining: 2m 36s
753:	learn: 214.5789510	total: 7m 56s	remaining: 2m 35s
754:	learn: 214.2668916	total: 7m 57s	remaining: 2m 34s
755:	learn: 213.9322127	total: 7m 57s	remaining: 2m 34s
756:	learn: 213.8110724	total: 7m 58s	remaining: 2m 33s
757:	learn: 213.4750058	total: 7m 59s	remaining: 2m 32s
758:	learn: 213.0481128	total: 7m 59s	remaining: 2m 32s
759:	learn: 212.6812068	total: 8m	remaining: 2m 31s
760:	learn: 212.3676788	total: 8m 1s	remaining: 2m 31s
761:	learn: 212.0148901	total: 8m 1s	remaining: 2m 30

892:	learn: 185.5632725	total: 9m 28s	remaining: 1m 8s
893:	learn: 185.3590639	total: 9m 29s	remaining: 1m 7s
894:	learn: 185.2534417	total: 9m 29s	remaining: 1m 6s
895:	learn: 184.9605518	total: 9m 30s	remaining: 1m 6s
896:	learn: 184.7976779	total: 9m 31s	remaining: 1m 5s
897:	learn: 184.7076036	total: 9m 31s	remaining: 1m 4s
898:	learn: 184.4557702	total: 9m 32s	remaining: 1m 4s
899:	learn: 184.4247629	total: 9m 32s	remaining: 1m 3s
900:	learn: 184.2980923	total: 9m 33s	remaining: 1m 3s
901:	learn: 184.0142756	total: 9m 34s	remaining: 1m 2s
902:	learn: 183.9085365	total: 9m 34s	remaining: 1m 1s
903:	learn: 183.7273518	total: 9m 35s	remaining: 1m 1s
904:	learn: 183.6814876	total: 9m 36s	remaining: 1m
905:	learn: 183.5152659	total: 9m 36s	remaining: 59.9s
906:	learn: 183.4507492	total: 9m 37s	remaining: 59.2s
907:	learn: 183.2121581	total: 9m 38s	remaining: 58.6s
908:	learn: 183.1663613	total: 9m 39s	remaining: 58s
909:	learn: 183.0685150	total: 9m 39s	remaining: 57.3s
910:	learn: 182

In [12]:
preds_xgbr

array([4292.541 , 6124.5996, 7230.8354, ..., 6476.4863, 4404.0684,
       7275.7324], dtype=float32)

In [11]:
preds_cbr

array([4322.44163736, 6211.46589669, 7345.01625626, ..., 6597.66795346,
       4466.50777813, 7261.28780213])

In [15]:
from sklearn.ensemble import VotingRegressor

models = [
    ('xgb', XGBRegressor(**best_params_xgbr1, random_state=rs)),
    ('cb', CatBoostRegressor(**best_params_catboost_r1, random_state=rs, silent=True))
]

voter = VotingRegressor(models)
voter.fit(X, y)
preds = voter.predict(X_t)

In [16]:
preds

array([4307.49132649, 6168.03275303, 7287.92585274, ..., 6537.07714079,
       4435.28806875, 7268.510112  ])

In [18]:
# create copies of the arrays
targets_c = np.copy(unique_targets)
preds_c = np.copy(preds)

# find the nearest value from the first array for each element in the second array
nearest_values = targets_c[np.abs(targets_c - preds_c[:, np.newaxis]).argmin(axis=1)]

# calculate the deviation of each element in the second array from its nearest value
deviations = np.sign(preds_c - nearest_values) * np.abs(preds_c - nearest_values)

# create the new array with replaced values
preds_replaced = nearest_values

# plot the deviations
px.line(deviations)

In [19]:
px.histogram(preds)

In [20]:
px.histogram(preds_replaced)

In [21]:
px.histogram(deviations)

In [22]:
deviations.std()

6.060974940409688

In [23]:
px.scatter(x=preds, y=deviations)

In [24]:
px.scatter(x=preds, y=preds_replaced, color=deviations)

In [25]:
submission = pd.DataFrame({'id': sample_submission.id, 'yield': preds})
submission.to_csv('../submissions/submission_8_O.csv', index=False)

LB: 361.15772

In [26]:
# kaggle submission file
submission = pd.DataFrame({'id': sample_submission.id, 'yield': preds_replaced})
submission.to_csv('../submissions/submission_8_R.csv', index=False)

LB: 361.27934